In [1]:
import os 
import numpy as np
import random
import math
from sklearn.metrics import average_precision_score
import pandas as pd

In [2]:
#從grid_search_weight中找尋不同的file 
path = '../Data/grid_search_weight/0113/'
files = os.listdir(path)
len(files)
np.load(path+files[0])['U'].shape

(1489, 64)

In [3]:
def square_sum(pars):
    all_squ_sum = []
    for par in pars:
        all_squ_sum.append(np.sum(np.multiply(par,par)))
    return all_squ_sum 
def shape_sum(pars):
    all_shape = []
    for par in pars:
        all_shape.append(par.shape)
    return all_shape
def relu(x):
    return np.maximum(0,x)  

def softmax(x):
    exp_x = np.exp(x)
    softmax_x = exp_x / np.sum(exp_x)
    return softmax_x 

def sigmoid(z):
    return 1 / (1 + np.exp(-z))  

In [5]:
user_following = np.load('../Data/npy/user_following_1489.npy')
all_3374 = np.load('../Data/npy/all_3374D.npy')
user_category = np.load('../Data/npy/user_category_1489.npy')
YouTuber_category = np.load('../Data/npy/YouTuber_category_0.7.npy')
active_users = np.load('../Data/npy/active_userID_1489.npy')
#The number of followers for each YouTuber
YouTuber_followers = np.sum(user_following, axis=0)
print(YouTuber_followers)
over5 = 0
for num in YouTuber_followers:
    if num >= 5:
        over5+=1
print('The num of followers over 5:',over5)
user_category_norm = np.zeros(user_category.shape)
for i in range(len(user_category)):
    user_category_norm[i] = user_category[i]/np.max(user_category[i])
print('user_category after normalized by max...')
print('user_category_norm shape ',user_category_norm.shape)
following_true = [0]*len(user_following)
for i in range(len(user_following)):
    each_user = []
    for j in range(len(user_following[i])):
        if user_following[i][j] == 1:
            each_user.append(j)
    following_true[i] = each_user
#print(following_true)
#最少跟最多的following 
minlen = 10000
maxlen = 0
num_of_follower = []
for i in range(len(following_true)):
    if len(following_true[i]) < minlen:
        minlen = len(following_true[i])
    if len(following_true[i]) > maxlen:
        maxlen = len(following_true[i])
    num_of_follower.append(len(following_true[i]))
print('Min number of followings ',minlen)
print('Max number of followings ',maxlen)
test_amount = 150
yt_test_amount = 18
user_idx = [i for i in range(len(user_following))]
#user_idx = user_idx_over10
#test_idx is the number of user for testing
random.seed(5)
test_idx = random.sample(user_idx,test_amount)
# Training  and Testing --New
train_t = [0]*(len(user_following))
train_f = [0]*(len(user_following))
# Testing 
test_t = [0]*test_amount
test_f = [0]*test_amount
test_pos = -1

for i in range(len(user_following)):
    t_for_train = []
    f_for_train = []
    if i not in test_idx: #if not in test id, just append it to true or false list
        for j in range(88):
            if user_following[i][j] == 1:
                t_for_train.append(j)
            else:
                f_for_train.append(j)
        train_t[i] = t_for_train
        train_f[i] = f_for_train
        
    else: #if in test id, choose 2 true and other 
        test_pos += 1
        temp_t = []
        temp_f = []
        for j in range(88):
            if user_following[i][j] == 1:
                temp_t.append(j)
            else:
                temp_f.append(j)
        #print(len(temp_t),math.ceil(0.5*len(temp_t)))
        t_for_test = random.sample(temp_t,math.ceil(0.5*len(temp_t)))
        f_for_test  = random.sample(temp_f,yt_test_amount-len(t_for_test))
        
        test_t[test_pos] = t_for_test
        test_f[test_pos] = f_for_test
        
        #other for training
        t_for_train = [item for item in temp_t if not item in t_for_test]
        #print(len(t_for_train ))
        f_for_train = [item for item in temp_f if not item in f_for_test]
        train_t[i] = t_for_train
        train_f[i] = f_for_train
total_test = 0
for t in test_t:
    total_test += len(t)
avg = total_test/test_amount
print(avg)

[180   2  20 385  21   3  28 163 628  57 303 564 134  29 246   7  76 322
  35  13  28  99  65   7 508 610 186 278 425 222  25  20 310 315   2  46
   5  90 100   3 463 271  33 461 152 321  16   9   5 151  15   4   1  29
 342  78  33 164   2  85 376   3  12 602   2   3  20 958  10  37 256 319
 149  23 736 154 382   2  49 972  74   2 477 107 364   7  54   5]
The num of followers over 5: 76
user_category after normalized by max...
user_category_norm shape  (1489, 17)
Min number of followings  5
Max number of followings  34
5.466666666666667


In [6]:
def getScoreMatrix(RS):
    #取出test的資料
    testRS = np.zeros((test_amount,yt_test_amount)) #shape 150*20
    target = np.zeros((test_amount,yt_test_amount))
    #test_t 是true的
    #test_f 是false的

    for z in range(test_amount):
        user_id = test_idx[z]
        #positive target YouTuber list
        youtube_t = test_t[z] 
        #not target YouTuber list
        youtube_f = test_f[z]

        #前兩個放target的RS
        for i in range(len(youtube_t)):
            testRS[z][i] = RS[z][youtube_t[i]]
            target[z][i] = 1
        for i in range(len(youtube_f)):
            testRS[z][i+len(youtube_t)] = RS[z][youtube_f[i]]
    sumtarget = 0
    for i in range(len(target)):
        #print(np.sum(target[i]))
        sumtarget += np.sum(target[i])
    print('num of positive data in testing:',sumtarget)
    print('total testing data:',test_amount*yt_test_amount)
    return target, testRS,sumtarget

def topN(sortlist,n):
    topList = []
    for i in range(n):
        topList.append(sortlist.index(max(sortlist)))
        #print(max(sortlist))
        #print(sortlist.index(max(sortlist)))
        sortlist[sortlist.index(max(sortlist))] = -1000000000
    return topList

def F1_score(prec,rec):
    f1 = (2*prec*rec)/(prec+rec)
    return f1

In [7]:
def getTOP1(target,testRS,sumtarget):
    print('top1')
    correct = 0
    for i in range(len(testRS)):
        top_0 = topN(list(testRS[i]),1) #取一個
        
        #print(top_0)
        if top_0[0] < int(np.sum(target[i])):
            correct += 1
    top1_prec = correct/len(testRS)
    top1_recall = correct/(sumtarget)
    print('prec ',top1_prec,'recall ',top1_recall)
    #f1 score
    print('F1_score:',F1_score(top1_prec,top1_recall))
def getTOP3(target,testRS,sumtarget):
    print('top3')
    correct = 0
    for i in range(len(testRS)):
        top_3 = topN(list(testRS[i]),3) #取一個
        
        #print(top_3)
        for j in range(len(top_3)):
            if top_3[j] < int(np.sum(target[i])):
                correct += 1
    top3_prec = correct/(len(testRS)*3)
    top3_recall = correct/(sumtarget)
    print('prec ',top3_prec,'recall ',top3_recall)
    #f1 score
    print('F1_score:',F1_score(top3_prec,top3_recall))
    
def getTOP5(target,testRS,sumtarget):
    print('top5')
    correct = 0
    for i in range(len(testRS)):
        top_5 = topN(list(testRS[i]),5) #取一個
       
        #print(top_5)
        for j in range(len(top_5)):
            if top_5[j] < int(np.sum(target[i])):
                correct += 1
    top5_prec = correct/(len(testRS)*5)
    top5_recall = correct/(sumtarget)
    print('prec ',top5_prec,'recall ',top5_recall)
    #f1 score
    print('F1_score:',F1_score(top5_prec,top5_recall))

In [8]:
"""
NDCG
https://daiwk.github.io/posts/nlp-ndcg.html
"""
# pre_list
"""
test_amount = 150
yt_test_amount = 20
"""
def NDCG(target,testRS):
    all_sort = []
    num_ndcg = 10
    pre_matrix = np.zeros(shape=(test_amount,yt_test_amount))
    for i in range(test_amount):
        top_n = topN(list(testRS[i]),num_ndcg) #取一個
        #print(top_n)
        all_sort.append(topN(list(testRS[i]),len(testRS[i])))
        for j in range(len(top_n)):
            pre_matrix[i][top_n[j]] = 1

    #Ideal DCG，理想状况下的DCG。也就是说，相关性完全由高到低排序时算出的DCG：
    def IDCG(ideal_list): #ideal_list example = [1,1,1,1,1,0,0,....]
        idcg=0
        #print('ideal',ideal_list)
        for i in range(len(ideal_list)):
            #print((2**true_list[i]-1),math.log2(i+2))
            idcg+= (2**ideal_list[i]-1)/ math.log2(i+2)
        #print('idcg',idcg)
        return idcg
    def DCG(prec_list): #找出前n名的[1,1,1,0,...]
        dcg=0
        print('prec',prec_list)
        for i in range(len(prec_list)):
            dcg+= (2**prec_list[i]-1)/ math.log2(i+2)
        #print('dcg',dcg)
        return dcg
    total_ndcg = 0
    
    for m in range(test_amount): # the number of testing users
        idcg = IDCG(target[m][:num_ndcg])
        pre_list = []
        least_pre_list = []
        for s in all_sort[m][:num_ndcg]:
            #print(s)
            #print(target[m][s])
            pre_list.append(target[m][s]) #把prec_list 的 score加進去
        for s in all_sort[m][num_ndcg:]:
            #print(s)
            #print(target[m][s])
            least_pre_list.append(target[m][s]) #把prec_list 的 score加進去
        dcg = DCG(pre_list)
        ndcg = dcg/idcg
        #print(ndcg)
        total_ndcg += ndcg
    avg_ndcg = total_ndcg/test_amount
    print('NDCG:',avg_ndcg)
    return pre_matrix,avg_ndcg

# MAP
"""
>>> y_true = np.array([0, 0, 1, 1])
>>> y_scores = np.array([0.1, 0.4, 0.35, 0.8])
>>> average_precision_score(y_true, y_scores)
"""
def MAP(target,pre_matrix):
    total_prec = 0
    for u in range(test_amount):
        y_true = target[u]
        y_scores = pre_matrix[u]
        total_prec+=average_precision_score(y_true, y_scores)
    Map_value = total_prec/test_amount
    print('MAP',Map_value)
    return Map_value

In [15]:
def testing(U, Y, A, E,Au, Ay, Aa, Av,Ave,B):
    print(U.shape)
    print(Y.shape)
    print(A.shape)
    print(np.max(Au))
    print(np.max(Ay))
    print(np.max(Aa))
    print(np.max(Av))
    print(np.max(B))
    result=np.zeros((test_amount,88))
    RS=np.zeros((test_amount,88))
    #test_idx --> Test 的 index
    sum_alpha = 0
    for s in range(test_amount):
        print(s,test_idx[s])

        yes=[]
        #sample=random.sample(train_t[test_idx[s]],len(train_t[test_idx[s]])) #從training part 的positive feedback 取出YouTuber 當成Auxilary
        sample = train_t[test_idx[s]]
        #sample=result_yes_id[now]
        alpha=np.zeros([len(sample)])

        for a in range(len(sample)):
            r =np.max(YouTuber_category[sample[a]]*user_category_norm[test_idx[s]]) #sample a 的category vec *user_category vec
            alpha_a = np.dot(Au[test_idx[s]][sample[a]],np.expand_dims(U[test_idx[s]],0).T)+np.dot(Ay[test_idx[s]][sample[a]],np.expand_dims(Y[sample[a]],0).T)+np.dot(Aa[test_idx[s]][sample[a]],
                    np.expand_dims(A[sample[a]],0).T)+ np.dot(Av[test_idx[s]][sample[a]],np.dot(Ave,np.expand_dims(all_3374[sample[a]],0).T))
            """
            relu part ...
            """
            alpha[a]=np.sum((relu(alpha_a)))*r
            """
            tanh part ...
            """
            #alpha[a]=np.sum((np.tanh(alpha_a)))*r
            
            
        mul=np.zeros((1,64))
        #print('alpha--------',alpha)
        #print('add alpha------------',np.add(alpha,0.000000001))
        added_alpha = np.add(alpha,0.000000001)
        norm_alpha = added_alpha/np.sum(added_alpha)
        print('alpha-----------',alpha)
        print('norm alpha--------------',norm_alpha)
        sum_alpha += np.sum(alpha)
        for i in range(len(sample)):
            mul+=norm_alpha[i]*A[sample[i]] #attention alpha*Ai part
        new_mul=mul+U[test_idx[s]]  #(U+auxilary)
    
        
        
        for k in range(88):
            result[s][k]=np.dot(new_mul,Y[k].T) #(U+auxilary)*photo latent factor
            RS[s][k] = np.dot(new_mul,Y[k].T)+np.dot(B[test_idx[s]],np.dot(E, all_3374[k].T))
            
            print('================================')
            print('U',np.sum(U[test_idx[s]] ))
            print('A',np.sum(mul))
            print('Y',np.sum(Y[k]))
            print('B',np.sum(B[test_idx[s]]))
            print('E',np.sum(np.dot(E, all_3374[k].T)))
            print('User',np.dot(U[test_idx[s]],Y[k].T))
            print('Aux',np.dot(mul,Y[k].T))
            print('Former',np.dot(new_mul,Y[k].T))
            print('Later',np.dot(B[test_idx[s]],np.dot(E, all_3374[k].T)))
            print('RS',np.dot(new_mul,Y[k].T)+np.dot(B[test_idx[s]],np.dot(E, all_3374[k].T)))
            print('--------------------------------')
            
    print('sum_alpha',sum_alpha)
    return RS

In [16]:
#Without Embedding
import os 
#從grid_search_weight中找尋不同的file 
path = '../Data/grid_search_weight/0113/'
all_files = os.listdir(path)
#print(files)
par_files = list(set([file.split('_Edims')[0] for file in all_files]))
print(par_files)
for par_file in par_files:
    NDCG_List = []
    MAP_List = []
    DIM_List = []
    csv_path = '../Data/grid_search_weight/CSV_Tan/'
    for file in all_files:
        if par_file in file:
            print(par_file,file)
            par_data = np.load(path+file)
            U = par_data['U']
            Y = par_data['Y']
            A = par_data['A']
            E = par_data['E']
            #W1 = par_data['W1']
            Wu = par_data['Wu']
            Wy = par_data['Wy']
            Wa = par_data['Wa']
            Wv = par_data['Wv']
            B = par_data['B']
            RS = testing(U, Y, A, E,Wu, Wy, Wa, Wv,B)
            target,testRS,sumtarget = getScoreMatrix(RS)
            getTOP1(target,testRS,sumtarget)
            getTOP3(target,testRS,sumtarget)
            getTOP5(target,testRS,sumtarget)
            pre_matrix,avg_ndcg = NDCG(target,testRS)
            Map_value = MAP(target,pre_matrix)
            NDCG_List.append(avg_ndcg)
            MAP_List.append(Map_value)
            DIM_List.append(file.split('Edims')[1].split('.npz')[0])
            print('--------------------------------------------------------------------------------------------')
    #print(NDCG_List)
    #print(DIM_List)
    result_dict = {'Dims':DIM_List,'NDCG':NDCG_List,'MAP':MAP_List}
    df = pd.DataFrame(result_dict)
    #df.to_csv(csv_path+par_file+'.csv',index=False)

['0.001_0.001_0.01_0.01']
0.001_0.001_0.01_0.01 0.001_0.001_0.01_0.01_Edims5.npz


TypeError: testing() missing 1 required positional argument: 'B'

In [17]:
#With Embedding
import os 
#從grid_search_weight中找尋不同的file 
path = '../Data/grid_search_weight/0113/'
all_files = os.listdir(path)
#print(files)
par_files = list(set([file.split('_Edims')[0] for file in all_files]))
print(par_files)
for par_file in par_files:
    NDCG_List = []
    MAP_List = []
    DIM_List = []
    csv_path = '../Data/grid_search_weight/CSV_Tan/'
    for file in all_files:
        if par_file in file:
            print(par_file,file)
            par_data = np.load(path+file)
            U = par_data['U']
            Y = par_data['Y']
            A = par_data['A']
            E = par_data['E']
            #W1 = par_data['W1']
            Wu = par_data['Wu']
            Wy = par_data['Wy']
            Wa = par_data['Wa']
            Wv = par_data['Wv']
            Wve = par_data['Wve']
            B = par_data['B']
            RS = testing(U, Y, A, E,Wu, Wy, Wa, Wv,Wve,B)
            target,testRS,sumtarget = getScoreMatrix(RS)
            getTOP1(target,testRS,sumtarget)
            getTOP3(target,testRS,sumtarget)
            getTOP5(target,testRS,sumtarget)
            pre_matrix,avg_ndcg = NDCG(target,testRS)
            Map_value = MAP(target,pre_matrix)
            NDCG_List.append(avg_ndcg)
            MAP_List.append(Map_value)
            DIM_List.append(file.split('Edims')[1].split('.npz')[0])
            print('--------------------------------------------------------------------------------------------')
    #print(NDCG_List)
    #print(DIM_List)
    result_dict = {'Dims':DIM_List,'NDCG':NDCG_List,'MAP':MAP_List}
    df = pd.DataFrame(result_dict)
    #df.to_csv(csv_path+par_file+'.csv',index=False)

['0.001_0.001_0.01_0.01']
0.001_0.001_0.01_0.01 0.001_0.001_0.01_0.01_Edims5.npz
(1489, 64)
(88, 64)
(88, 64)
0.0012915093
0.0012915089
0.0012915093
0.0012915087
0.34095445
0 1275
alpha----------- [3.52881002e-10 1.74951276e-10 0.00000000e+00 1.61831380e-10
 0.00000000e+00 0.00000000e+00 0.00000000e+00]
norm alpha-------------- [0.175935   0.15279619 0.1300447  0.15109001 0.1300447  0.1300447
 0.1300447 ]
U -1.4698306e-07
A -0.1375292774682748
Y -8.567772
B 0.13109928
E -23.236380965617137
User -6.917735e-08
Aux [0.42564896]
Former [0.42564889]
Later -0.3800180216441399
RS [0.04563086]
--------------------------------
U -1.4698306e-07
A -0.1375292774682748
Y 11.857591
B 0.13109928
E -14.944007650683663
User 4.5118355e-07
Aux [-2.56422483]
Former [-2.56422438]
Later -0.36484654692133217
RS [-2.92907093]
--------------------------------
U -1.4698306e-07
A -0.1375292774682748
Y 9.526461
B 0.13109928
E -13.283571980805295
User 4.0286625e-07
Aux [-2.17440557]
Former [-2.17440516]
Later -0.2

E 13.07999597130895
User -0.08717205
Aux [-0.97856743]
Former [-1.06573948]
Later 0.37319695692330673
RS [-0.69254253]
--------------------------------
U -0.15049331
A -0.49762723862815594
Y 10.964575
B 0.15692618
E -12.217182981661518
User -0.19203861
Aux [-1.94858754]
Former [-2.14062611]
Later -0.39341191471070946
RS [-2.53403802]
--------------------------------
U -0.15049331
A -0.49762723862815594
Y 3.4917996
B 0.15692618
E -17.53783506719229
User 0.036475454
Aux [-0.11627981]
Former [-0.07980435]
Later -0.6195123266530529
RS [-0.69931668]
--------------------------------
U -0.15049331
A -0.49762723862815594
Y 6.10773
B 0.15692618
E -1.2265756534904775
User -0.023348846
Aux [0.61136476]
Former [0.5880159]
Later -0.01830990149457703
RS [0.569706]
--------------------------------
U -0.15049331
A -0.49762723862815594
Y 9.762316
B 0.15692618
E -9.852815709783025
User -0.16146399
Aux [-1.30322316]
Former [-1.46468714]
Later -0.3316194759502482
RS [-1.79630662]
-------------------------

U 0.01284976
A 0.4845013876252149
Y 8.212267
B 0.50695175
E 13.07999597130895
User -0.00969229
Aux [0.17373698]
Former [0.16404469]
Later 1.2691401509118077
RS [1.43318484]
--------------------------------
U 0.01284976
A 0.4845013876252149
Y 10.964575
B 0.50695175
E -12.217182981661518
User -0.028237991
Aux [-1.85461262]
Former [-1.88285061]
Later -1.1832048843775897
RS [-3.06605549]
--------------------------------
U 0.01284976
A 0.4845013876252149
Y 3.4917996
B 0.50695175
E -17.53783506719229
User -0.0043151355
Aux [-0.8881723]
Former [-0.89248743]
Later -1.925646142428369
RS [-2.81813357]
--------------------------------
U 0.01284976
A 0.4845013876252149
Y 6.10773
B 0.50695175
E -1.2265756534904775
User 0.022230435
Aux [1.57390311]
Former [1.59613354]
Later 0.025659049871734202
RS [1.62179259]
--------------------------------
U 0.01284976
A 0.4845013876252149
Y 9.762316
B 0.50695175
E -9.852815709783025
User -0.020879881
Aux [-1.38879147]
Former [-1.40967136]
Later -0.93506584469172

U -0.0007207567
A 0.007260846111276531
Y 9.762316
B 0.42464063
E -9.852815709783025
User 0.0001022403
Aux [-0.21797604]
Former [-0.2178738]
Later -0.8194955169526138
RS [-1.03736932]
--------------------------------
U -0.0007207567
A 0.007260846111276531
Y 10.693502
B 0.42464063
E -15.612173216424484
User -2.0203704e-05
Aux [-0.43092565]
Former [-0.43094586]
Later -1.373841778564828
RS [-1.80478763]
--------------------------------
U -0.0007207567
A 0.007260846111276531
Y 8.51086
B 0.42464063
E -4.733643588977449
User 0.00019365415
Aux [-0.16105267]
Former [-0.16085901]
Later -0.3754147804419512
RS [-0.53627379]
--------------------------------
U -0.0007207567
A 0.007260846111276531
Y -0.88510704
B 0.42464063
E -9.361940614663453
User 0.00014912055
Aux [-0.34350396]
Former [-0.34335484]
Later -0.8889113405622219
RS [-1.23226618]
--------------------------------
U -0.0007207567
A 0.007260846111276531
Y 9.847497
B 0.42464063
E -6.853121093677823
User -1.0450545e-05
Aux [0.20889857]
Forme

Later -2.27607678002655
RS [-2.67024952]
--------------------------------
U -2.465519e-10
A -0.44392796610554797
Y 6.10773
B 0.6371409
E -1.2265756534904775
User -2.543185e-09
Aux [0.11756675]
Former [0.11756675]
Later -0.27602812667622517
RS [-0.15846137]
--------------------------------
U -2.465519e-10
A -0.44392796610554797
Y 9.762316
B 0.6371409
E -9.852815709783025
User 4.2835768e-10
Aux [-0.76244661]
Former [-0.76244661]
Later -1.4093123140433859
RS [-2.17175893]
--------------------------------
U -2.465519e-10
A -0.44392796610554797
Y 10.693502
B 0.6371409
E -15.612173216424484
User 7.9774853e-10
Aux [-0.79777291]
Former [-0.79777291]
Later -1.8521114242505363
RS [-2.64988433]
--------------------------------
U -2.465519e-10
A -0.44392796610554797
Y 8.51086
B 0.6371409
E -4.733643588977449
User 1.110047e-09
Aux [-0.88123273]
Former [-0.88123273]
Later -0.7071591726316198
RS [-1.5883919]
--------------------------------
U -2.465519e-10
A -0.44392796610554797
Y -0.88510704
B 0.637

...

Later -0.7639363148501308
RS [2.25390471]
--------------------------------
U -0.00084870844
A -0.0011860725353471935
Y 11.787582
B 0.37736547
E -7.4281597583122725
User 0.0019330772
Aux [-3.66725353]
Former [-3.66532045]
Later -0.5379528649833616
RS [-4.20327332]
--------------------------------
U -0.00084870844
A -0.0011860725353471935
Y 10.874919
B 0.37736547
E 12.007420830742355
User 0.0019550682
Aux [-3.83807801]
Former [-3.83612294]
Later 0.9276323969007012
RS [-2.90849054]
--------------------------------
U -0.00084870844
A -0.0011860725353471935
Y -1.4099624
B 0.37736547
E 13.003293957057036
User -0.0015631409
Aux [2.34519782]
Former [2.34363468]
Later 0.9779757582826991
RS [3.32161044]
--------------------------------
U -0.00084870844
A -0.0011860725353471935
Y 9.541912
B 0.37736547
E -15.320753668079375
User 0.00066792674
Aux [-0.87915365]
Former [-0.87848573]
Later -1.1023681543433628
RS [-1.98085388]
--------------------------------
U -0.00084870844
A -0.0011860725353471935


Later 0.019839803234821304
RS [-2.28005434]
--------------------------------
U -0.10395353
A 0.42570074182043527
Y 6.0416784
B 0.12032272
E -11.337225865498393
User 0.018461121
Aux [-1.15300408]
Former [-1.13454296]
Later -0.20964619875639384
RS [-1.34418916]
--------------------------------
U -0.10395353
A 0.42570074182043527
Y 12.7229
B 0.12032272
E -16.939614022613632
User 0.020744767
Aux [-1.99710145]
Former [-1.97635668]
Later -0.28407367049083226
RS [-2.26043035]
--------------------------------
147 114
alpha----------- [1.98443701e-06 0.00000000e+00 1.87451253e-05 2.81354209e-05]
norm alpha-------------- [4.06277537e-02 2.04628771e-05 3.83599660e-01 5.75752124e-01]
U 0.0012393352
A -0.9442222401776803
Y -8.567772
B 0.18590438
E -23.236380965617137
User 0.001741322
Aux [0.12881654]
Former [0.13055786]
Later -0.8507018327575705
RS [-0.72014397]
--------------------------------
U 0.0012393352
A -0.9442222401776803
Y 11.857591
B 0.18590438
E -14.944007650683663
User -0.0052628065
Au

RS [-0.55610338]
--------------------------------
U 0.0012393352
A -0.9442222401776803
Y 10.874919
B 0.18590438
E 12.007420830742355
User -0.006401913
Aux [-0.16999428]
Former [-0.17639619]
Later 0.44867824536727513
RS [0.27228205]
--------------------------------
U 0.0012393352
A -0.9442222401776803
Y -1.4099624
B 0.18590438
E 13.003293957057036
User 0.0037820446
Aux [0.00915478]
Former [0.01293682]
Later 0.4491798250748909
RS [0.46211665]
--------------------------------
U 0.0012393352
A -0.9442222401776803
Y 9.541912
B 0.18590438
E -15.320753668079375
User -0.0017271276
Aux [-0.18387903]
Former [-0.18560616]
Later -0.5691979831800138
RS [-0.75480414]
--------------------------------
U 0.0012393352
A -0.9442222401776803
Y 12.657774
B 0.18590438
E -11.09912432160232
User -0.0057826303
Aux [-0.26623275]
Former [-0.27201538]
Later -0.40749095273213287
RS [-0.67950633]
--------------------------------
U 0.0012393352
A -0.9442222401776803
Y -16.43667
B 0.18590438
E 0.10288551922275102
Use

U -5.2687657e-05
A 1.9888397288333408
Y 1.9844644
B 0.729702
E 7.793777512034221
User 0.00010083486
Aux [-1.08721863]
Former [-1.0871178]
Later 1.1290856819614685
RS [0.04196788]
--------------------------------
U -5.2687657e-05
A 1.9888397288333408
Y -7.1692333
B 0.729702
E -10.607900957655357
User -0.00012648878
Aux [2.4621181]
Former [2.46199161]
Later -1.590007929373456
RS [0.87198368]
--------------------------------
U -5.2687657e-05
A 1.9888397288333408
Y 11.787582
B 0.729702
E -7.4281597583122725
User 0.00016847976
Aux [-2.53098169]
Former [-2.53081321]
Later -1.1256064190816337
RS [-3.65641963]
--------------------------------
U -5.2687657e-05
A 1.9888397288333408
Y 10.874919
B 0.729702
E 12.007420830742355
User 0.00017919447
Aux [-2.74132547]
Former [-2.74114628]
Later 1.7250775047459417
RS [-1.01606877]
--------------------------------
U -5.2687657e-05
A 1.9888397288333408
Y -1.4099624
B 0.729702
E 13.003293957057036
User -0.00015841551
Aux [2.76963034]
Former [2.76947192]
La

RS [0.7749503]
--------------------------------
U -2.0378502e-10
A 0.008959824812336592
Y 11.787582
B 0.5889473
E -7.4281597583122725
User 4.5661633e-10
Aux [-2.11639441]
Former [-2.11639441]
Later -0.9187287156258637
RS [-3.03512313]
--------------------------------
U -2.0378502e-10
A 0.008959824812336592
Y 10.874919
B 0.5889473
E 12.007420830742355
User 5.051958e-10
Aux [-2.44805755]
Former [-2.44805755]
Later 1.434151620389747
RS [-1.01390593]
--------------------------------
U -2.0378502e-10
A 0.008959824812336592
Y -1.4099624
B 0.5889473
E 13.003293957057036
User -5.7076766e-10
Aux [1.91592844]
Former [1.91592844]
Later 1.5269301436105926
RS [3.44285859]
--------------------------------
U -2.0378502e-10
A 0.008959824812336592
Y 9.541912
B 0.5889473
E -15.320753668079375
User 7.328607e-11
Aux [-0.63633239]
Former [-0.63633239]
Later -1.7348632729497941
RS [-2.37119567]
--------------------------------
U -2.0378502e-10
A 0.008959824812336592
Y 12.657774
B 0.5889473
E -11.09912432160

In [94]:
for i in range(len(NDCG_List)):
    print(NDCG_List[i],MAP_List[i])

# NDCG For Different Dimensions

In [111]:
######## code here !!!!

(10, 20)

In [69]:
def topN(sortlist,n):
    topList = []
    for i in range(n):
        topList.append(sortlist.index(max(sortlist)))
        #print(max(sortlist))
        #print(sortlist.index(max(sortlist)))
        sortlist[sortlist.index(max(sortlist))] = -1000000000
    return topList

In [70]:
count_0_all = []
for i in range(len(testRS)):
    top_0 = topN(list(testRS[i]),int(np.sum(target[i])))
    count_0_all.append(top_0)
    print(top_0)

acc_0 = 0
total = 0
for i in range(len(count_0_all)):
    for j in range(len(count_0_all[i])):
        #print(int(np.sum(target[i])))
        total+=int(np.sum(target[i]))
        if count_0_all[i][j] < int(np.sum(target[i])): #代表是0或1 (也就是target)
            acc_0 += 1
avg_acc = acc_0/100
print('avg_accuarcy for count_0:',avg_acc)
print(acc_0)

[0, 2, 1]
[3, 6, 2]
[1, 2, 13, 4, 5, 3, 17]
[1, 10, 8, 2, 5, 4]
[4, 1, 12]
[1, 15, 11]
[2, 1, 10, 0]
[3, 2, 5, 7, 4, 18]
[3, 18, 8, 5, 13]
[12, 16, 7, 0, 9]
avg_accuarcy for count_0: 0.24
24


# TOP1,TOP3,TOP5

In [71]:
def F1_score(prec,rec):
    f1 = (2*prec*rec)/(prec+rec)
    return f1

# NDCG 

In [172]:
a_list = [0.02162337, 0.02162659, 0.00240219, 0.00780985, 0.02162318, 0.00780592, 0.00780849]
softmax(a_list)

array([0.14409628, 0.14409674, 0.14135303, 0.14211949, 0.14409625,
       0.14211893, 0.14211929])